<a href="https://colab.research.google.com/github/vdlphm/CS403-Fall-2023/blob/main/hw4.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Homework 4: 6-DoF Open-chain Arm 

<img src="https://github.com/DARoSLab/CS403-Intro-Robotics/blob/main/arm.png?raw=true" width="400">






In [4]:
#install meshcat visualizer 
!git clone https://github.com/RussTedrake/meshcat-python --branch colab --recursive
!pip3 install u-msgpack-python
!git clone https://github.com/DARoSLab/CS403-Intro-Robotics
import sys
sys.path.append('/content/meshcat-python/src')

Cloning into 'meshcat-python'...
remote: Enumerating objects: 948, done.
remote: Counting objects: 100% (7/7), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 948 (delta 0), reused 7 (delta 0), pack-reused 941
Receiving objects: 100% (948/948), 180.61 KiB | 4.75 MiB/s, done.
Resolving deltas: 100% (543/543), done.
Submodule 'meshcat/viewer' (https://github.com/rdeits/meshcat.git) registered for path 'src/meshcat/viewer'
Cloning into '/content/meshcat-python/src/meshcat/viewer'...
remote: Enumerating objects: 1366, done.        
remote: Counting objects: 100% (264/264), done.        
remote: Compressing objects: 100% (107/107), done.        
remote: Total 1366 (delta 143), reused 245 (delta 134), pack-reused 1102        
Receiving objects: 100% (1366/1366), 3.95 MiB | 20.21 MiB/s, done.
Resolving deltas: 100% (820/820), done.
Submodule path 'src/meshcat/viewer': checked out '85fd641e8897ffe453502e0ec152225562999b0b'
Looking in indexes: https://pypi.org/simple, https:/

In [5]:
#Python libraries
from meshcat.jupyter import JupyterVisualizer
import meshcat.geometry as g
import meshcat.transformations as tf
from meshcat.geometry import Box, Mesh, Sphere, MeshLambertMaterial, DaeMeshGeometry
import numpy as np
import os
import time
mesh_path =  '/content/CS403-Intro-Robotics/hws/hw4/meshes/'

In [6]:
def generate_transformation_matrix(xyz=[0,0,0], rpy=[0,0,0]):
    Rx = tf.rotation_matrix(rpy[0], [1, 0, 0])[:3, :3]
    Ry = tf.rotation_matrix(rpy[1], [0, 1, 0])[:3, :3]
    Rz = tf.rotation_matrix(rpy[2], [0, 0, 1])[:3, :3]    

    R = np.matmul(Rz, np.matmul(Ry, Rx))
    T = np.zeros((4,4))
    T[:3, :3] = R
    T[0, 3] = xyz[0]
    T[1, 3] = xyz[1]
    T[2, 3] = xyz[2]
    T[3, 3] = 1.0
    return T
    

# Visualize robot

In [16]:
def visualize_robot():
  vis = JupyterVisualizer()
  vis["arm/base"].set_object(
      g.DaeMeshGeometry.from_file(
          os.path.join(mesh_path, 'arm_base.dae')), MeshLambertMaterial(color=0xA7A7A7)) 
  vis["arm/base/link1"].set_object(
      g.DaeMeshGeometry.from_file(
          os.path.join(mesh_path, 'arm_link1.dae')), MeshLambertMaterial(color=0x424242)
  )
  vis["arm/base/link1/link2"].set_object(
      g.DaeMeshGeometry.from_file(
          os.path.join(mesh_path, 'arm_link2.dae')), MeshLambertMaterial(color=0x3633FF)
  )
  vis["arm/base/link1/link2/link3"].set_object(
      g.DaeMeshGeometry.from_file(
          os.path.join(mesh_path, 'arm_link3.dae')), MeshLambertMaterial(color=0xf25c19)
  )
  vis["arm/base/link1/link2/link3/link4"].set_object(
      g.DaeMeshGeometry.from_file(
          os.path.join(mesh_path, 'arm_link4.dae')), MeshLambertMaterial(color=0x000000)
  )
  vis["arm/base/link1/link2/link3/link4/link5"].set_object(
      g.DaeMeshGeometry.from_file(
          os.path.join(mesh_path, 'arm_link5.dae')), MeshLambertMaterial(color=0xA7A7A7)
  )
  vis["arm/base/link1/link2/link3/link4/link5/ee"].set_object(
      g.DaeMeshGeometry.from_file(
          os.path.join(mesh_path, 'arm_ee.dae')), MeshLambertMaterial(color=0xFF4265)
  )
  return vis

# Q.1 (a) [20 pts] Assemble the robot based on the diagram and complete a forward kinematics function
<img src="https://github.com/DARoSLab/CS403-Intro-Robotics/blob/main/figures/robot-configuration.png?raw=true" width="600">


In [81]:
def ForwardKinematics(viz, q=[0, 0, 0, 0, 0, 0]):
  base_to_joint1 = generate_transformation_matrix(xyz=[0.0, 0.0, 0.0], rpy=[0,0,q[0]])
  # Fill your code here
  joint1_to_joint2 = generate_transformation_matrix(xyz=[0.0, 0.0, 0.15], rpy=[0,q[1],0])
  joint2_to_joint3 = generate_transformation_matrix(xyz=[0.23, 0.0, 0.0], rpy=[0,q[2],0])
  joint3_to_joint4 = generate_transformation_matrix(xyz=[0.13, 0.0, 0.0], rpy=[q[3],0,0])
  joint4_to_joint5 = generate_transformation_matrix(xyz=[0.09, 0.0, 0.0], rpy=[0,q[4],0])
  joint5_to_joint6 = generate_transformation_matrix(xyz=[0.06, 0.0, 0.0], rpy=[q[5],0,0])
  joint6_to_ee = generate_transformation_matrix(xyz=[0.045, 0.0, 0.0], rpy=[0,0,0])

  vis["arm/base/link1/ee"].set_transform(base_to_joint1)
  # Fill your code 
  vis["arm/base/link1/link2"].set_transform(joint1_to_joint2)
  vis["arm/base/link1/link2/link3"].set_transform(joint2_to_joint3)
  vis["arm/base/link1/link2/link3/link4"].set_transform(joint3_to_joint4)
  vis["arm/base/link1/link2/link3/link4/link5"].set_transform(joint4_to_joint5)
  vis["arm/base/link1/link2/link3/link4/link5/ee"].set_transform(joint5_to_joint6)
  
  base_to_ee = base_to_joint1 @ joint1_to_joint2 @ joint2_to_joint3 @ joint3_to_joint4 @ joint4_to_joint5  @ joint5_to_joint6 @ joint6_to_ee

  return base_to_ee

# Q 1.(b) [10 pts] Test the implemented forward kinematics function with your own test configurations and compare the results with your expectation. 
1. List the configurations and expected end-effector position/orientation that you select (at least two configurations should be tested)
2. Give a short explanation why you choose the configuration

In [93]:
vis1 = visualize_robot()
q_test = [0,0,0,0,0,0] # Fill your code
EE = ForwardKinematics(vis1, q = q_test)
print(EE)

[[1.    0.    0.    0.555]
 [0.    1.    0.    0.   ]
 [0.    0.    1.    0.15 ]
 [0.    0.    0.    1.   ]]


In [94]:
vis2 = visualize_robot()
q_test = [0,-np.pi/2,0,0,0,0] # Fill your code
EE = ForwardKinematics(vis2, q = q_test)
print(EE)

[[ 6.12323400e-17  0.00000000e+00 -1.00000000e+00  3.39839487e-17]
 [ 0.00000000e+00  1.00000000e+00  0.00000000e+00  0.00000000e+00]
 [ 1.00000000e+00  0.00000000e+00  6.12323400e-17  7.05000000e-01]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  1.00000000e+00]]


1/ 
q = [0,0,0,0,0,0]
expected EE at
[
  [1,0,0,0.555]
  [0,1,0,0]
  [0,0,1,0.15]
  [0,0,0,1]
]
 This is to test in initial position, EE is at the right point.

2/
q = [0,-pi/2,0,0,0,0]
expected
[
  [0,0,-1,0]
  [0,1,0,0]
  [0,0,0,7.05]
  [0,0,0,1]
]
This is to test in an upright position to see if the EE is at max z.

# Q.2 [10 pts] Move the robot to the following configurations and report the end-effector position (3-dim vector) and orientation (SO(3)) as well screen shots of the scene in both configurations.


1.   $q_1 =(0, \frac{π}{4}, 0.5, 0.5, 0, 0)$ 
2.   $q_2 =(\frac{π}{2}, \frac{π}{6}, 0.0, 0.5, 0, \frac{π}{8})$



In [95]:
vis3 = visualize_robot()
# Fill your code here
q_test = [0,np.pi/4,0.5,0.5,0,0] # Fill your code
EE = ForwardKinematics(vis3, q = q_test)
print(EE)

[[ 0.28153953  0.4600326   0.84208402  0.25413491]
 [ 0.          0.87758256 -0.47942554  0.        ]
 [-0.95954963  0.13497724  0.24707418 -0.32448819]
 [ 0.          0.          0.          1.        ]]


In [96]:
vis4 = visualize_robot()
# Fill your code here
q_test = [np.pi/2,np.pi/6,0,0.5,0,np.pi/8] # Fill your code
EE = ForwardKinematics(vis4, q = q_test)
print(EE)

[[ 5.30287619e-17 -6.27312356e-01  7.78767749e-01  2.94309629e-17]
 [ 8.66025404e-01  3.89383875e-01  3.13656178e-01  4.80644099e-01]
 [-5.00000000e-01  6.74432655e-01  5.43268437e-01 -1.27500000e-01]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  1.00000000e+00]]


# Q3 [10 pts]. Animate the robot moving from $q_0→q_f$ where. 
\begin{align}
\mathbf{q}_{0} &= [0, 0, 0, 0, 0, 0]\\
\mathbf{q}_{f} &= [0.8, 0, -0.5, -0.5, 1.2, 0]\\
\end{align}
**Use linear interpolation to obtain the intermediate configurations. i.e $\mathbf{q}(\alpha)=(1-\alpha)\mathbf{q}_0 + \alpha*\mathbf{q}_f$ where $\alpha \in [0, 1]$**

In [105]:
# Fill your interporation code here 
# (tip: use 'time.sleep(0.05)' to slow down your animation)
vis5 = visualize_robot()
q0 = np.array([0,0,0,0,0,0])
qf = np.array([0.8,0,-0.5,-0.5,1.2,0])
size = 201
delta_a = 1 / size
a = 0
for i in range(size):
  qa = (1 - a) * q0 + a * qf
  a += delta_a
  ForwardKinematics(vis5, qa)
  time.sleep(0.05)